In [91]:
!bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh

In [92]:
!bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh; bash get_train_data.sh

In [132]:
!cat train_human*.log > models/20192009_9/train.csv

In [133]:
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import pickle
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [134]:
!cat models/20192009_9/train.csv | wc -l

10635


In [135]:
!ls models/20192009_9/

train.csv  train_human.log  train_human_2.log


In [136]:
features = ["f" + str(i) for i in range(0,33)]
label = ["action"]

headers = features + label

df = pd.read_csv('models/20192009_9/train.csv', 
                 sep = ',', 
                 header = None,
                 names = headers)
df

f0  f1  f2  f3  f4  f5  f6  f7  f8  f9  ...  f24  f25  f26  f27  f28  \
0       5  -1   1   7  -1   2   3   8   0  -2  ...   -1   -2    2    2   -1   
1       5  -1   1   7  -1   2   3   8   0  -2  ...   -1   -2    2    2   -1   
2       5  -1   1   7  -1   2   3   8   0  -2  ...    0   -2    2    2   -1   
3       5  -1   1   7  -1   2   3   9   0  -2  ...    0   -2    2    2   -1   
4       5  -1   1   7  -1   2   3   9   0  -2  ...    0   -2    2    2   -1   
...    ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...  ...  ...  ...  ...  ...   
10630   1  -3   4   3   1  -2   2   2   0  -1  ...    0    0    2    9   -1   
10631   1  -3   4   2   1  -2   2   2   0  -1  ...    0    0    2    9   -1   
10632   1  -3   4   2   1  -2   2   2   0  -1  ...    1    0    2    9   -1   
10633   1  -3   4   2   1  -2   2   1   0  -1  ...    1    0    2    9   -1   
10634   1  -3   4   2   1  -2   2   1   0  -1  ...    1    0    2    9   -1   

       f29  f30  f31  f32  action  
0       -1    4    5   -1       3  
1       -1    4    5   -1       3  
2       -1    4    5   -1       3  
3       -1    4    5   -1       3  
4       -1    4    5   -1       3  
...    ...  ...  ...  ...     ...  
10630   -2    2    3   -1       3  
10631   -2    2    3   -1       3  
10632   -2    2    3   -1       3  
10633   -2    2    3   -1       3  
10634   -2    2    3   -1       3  

[10635 rows x 34 columns]

In [137]:
print("headers length: {}, df lenght: {}".format(len(headers), len(df)))

headers length: 34, df lenght: 10635


In [138]:
df["f0"].value_counts()

1    1369
3    1247
4    1227
5    1222
6    1179
2    1178
7    1152
8    1055
9    1006
Name: f0, dtype: int64

In [139]:
print("different actions count \n{}".format(df.drop_duplicates()['action'].value_counts()))

different actions count 
0     3049
1     2855
4     1354
5     1295
3       39
2       16
15       1
Name: action, dtype: int64


In [140]:
print("no of states without duplicates: {}".format(len(df.drop_duplicates())))

no of states without duplicates: 8609


In [141]:
y_train_all = df["action"]
X_train_all = df.drop(columns="action")

In [142]:
print("no of states without duplicates and action column: {}".format(len(X_train_all.drop_duplicates())))

no of states without duplicates and action column: 7074


In [143]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [105]:
# X_train_all[["f0", "f1"]]

In [149]:
def evaluate_model(xtrain, ytrain, xtest, ytest, model):
    y_pred_test = model.predict(xtest)
    y_pred_train = model.predict(xtrain)
    test_accuracy = accuracy_score(ytest, y_pred_test)
    train_accuracy = accuracy_score(ytrain, y_pred_train)
    print('Training accuracy: {0:.2f}, evaluation accuracy: {1:.2f}'.format(train_accuracy, test_accuracy))


Basic logisting regresion

In [164]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, test_size=0.2)

classifier = LogisticRegression().fit(X_train_all, y_train_all)

In [165]:
evaluate_model(X_train, y_train, X_test, y_test, classifier)

Training accuracy: 0.46, evaluation accuracy: 0.48


In [166]:
pickle.dump(classifier, open("ai_model_logit.pkl","wb"))

xgboost

In [155]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, 
                                                    test_size=0.2, random_state=7)

xgb_model = XGBClassifier(n_estimators=500).fit(X_train, y_train,eval_set = [[X_test, y_test]], verbose = 1)

[0]	validation_0-merror:0.534086
[1]	validation_0-merror:0.51528
[2]	validation_0-merror:0.51622
[3]	validation_0-merror:0.511048
[4]	validation_0-merror:0.512459
[5]	validation_0-merror:0.503056
[6]	validation_0-merror:0.510108
[7]	validation_0-merror:0.503996
[8]	validation_0-merror:0.502586
[9]	validation_0-merror:0.505407
[10]	validation_0-merror:0.501175
[11]	validation_0-merror:0.495534
[12]	validation_0-merror:0.494593
[13]	validation_0-merror:0.489422
[14]	validation_0-merror:0.486601
[15]	validation_0-merror:0.486601
[16]	validation_0-merror:0.48284
[17]	validation_0-merror:0.48237
[18]	validation_0-merror:0.480019
[19]	validation_0-merror:0.478608
[20]	validation_0-merror:0.475317
[21]	validation_0-merror:0.473437
[22]	validation_0-merror:0.473437
[23]	validation_0-merror:0.469676
[24]	validation_0-merror:0.470616
[25]	validation_0-merror:0.473907
[26]	validation_0-merror:0.472967
[27]	validation_0-merror:0.471086
[28]	validation_0-merror:0.467795
[29]	validation_0-merror:0.4

[239]	validation_0-merror:0.370475
[240]	validation_0-merror:0.369064
[241]	validation_0-merror:0.367184
[242]	validation_0-merror:0.368594
[243]	validation_0-merror:0.368124
[244]	validation_0-merror:0.368124
[245]	validation_0-merror:0.368594
[246]	validation_0-merror:0.370005
[247]	validation_0-merror:0.368594
[248]	validation_0-merror:0.369064
[249]	validation_0-merror:0.368124
[250]	validation_0-merror:0.369064
[251]	validation_0-merror:0.368594
[252]	validation_0-merror:0.367184
[253]	validation_0-merror:0.366714
[254]	validation_0-merror:0.366244
[255]	validation_0-merror:0.366244
[256]	validation_0-merror:0.366714
[257]	validation_0-merror:0.368124
[258]	validation_0-merror:0.367654
[259]	validation_0-merror:0.368594
[260]	validation_0-merror:0.368124
[261]	validation_0-merror:0.369064
[262]	validation_0-merror:0.369064
[263]	validation_0-merror:0.369064
[264]	validation_0-merror:0.369535
[265]	validation_0-merror:0.369064
[266]	validation_0-merror:0.369064
[267]	validation_0-m

[475]	validation_0-merror:0.35355
[476]	validation_0-merror:0.35355
[477]	validation_0-merror:0.353079
[478]	validation_0-merror:0.352609
[479]	validation_0-merror:0.350729
[480]	validation_0-merror:0.351669
[481]	validation_0-merror:0.352139
[482]	validation_0-merror:0.351199
[483]	validation_0-merror:0.351669
[484]	validation_0-merror:0.351669
[485]	validation_0-merror:0.351199
[486]	validation_0-merror:0.351199
[487]	validation_0-merror:0.351199
[488]	validation_0-merror:0.351669
[489]	validation_0-merror:0.351199
[490]	validation_0-merror:0.351199
[491]	validation_0-merror:0.351199
[492]	validation_0-merror:0.351199
[493]	validation_0-merror:0.351199
[494]	validation_0-merror:0.351199
[495]	validation_0-merror:0.350259
[496]	validation_0-merror:0.350259
[497]	validation_0-merror:0.351199
[498]	validation_0-merror:0.351199
[499]	validation_0-merror:0.351199


In [156]:
evaluate_model(X_train, y_train, X_test, y_test, xgb_model)

Training accuracy: 0.70, evaluation accuracy: 0.65


In [112]:
# xgb_model = XGBClassifier(n_estimators=500).fit(X_train_all, y_train_all)

In [157]:
pickle.dump(xgb_model, open("ai_model_xgb.pkl","wb"))

random forest model

In [158]:
forest_model = RandomForestClassifier(random_state=1, n_estimators=100)
forest_model.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [126]:
evaluate_model(X_train, y_train, X_test, y_test, forest_model)

Training accuracy: 0.78, evaluation accuracy: 0.40


In [159]:
pickle.dump(forest_model, open("ai_model_forest.pkl","wb"))

In [84]:
# min_max_scaler = MinMaxScaler()
# np_scaled = min_max_scaler.fit_transform(df)
# df_normalized = pd.DataFrame(np_scaled)
# df_normalized.columns = feature_cols + ['Class']

In [85]:
# def make_crosses(X_train, X_validation, degree=2):
#   from sklearn.preprocessing import PolynomialFeatures
#   poly = PolynomialFeatures(degree=degree)
#   X_train_poly = poly.fit_transform(X_train)
#   X_validation_poly = poly.transform(X_validation)
#   return X_train_poly, X_validation_poly

In [160]:
mlp_model = MLPClassifier(solver='adam', alpha=1e-5, 
                    hidden_layer_sizes=(24, 24), 
                          random_state=1, verbose=True)

mlp_model.fit(X_train_all, y_train_all)

Iteration 1, loss = 1.97619891
Iteration 2, loss = 1.41356408
Iteration 3, loss = 1.33705116
Iteration 4, loss = 1.30678281
Iteration 5, loss = 1.28582996
Iteration 6, loss = 1.27266998
Iteration 7, loss = 1.26010030
Iteration 8, loss = 1.24913364
Iteration 9, loss = 1.23654757
Iteration 10, loss = 1.22493529
Iteration 11, loss = 1.21325805
Iteration 12, loss = 1.20306421
Iteration 13, loss = 1.19039897
Iteration 14, loss = 1.18434827
Iteration 15, loss = 1.16904483
Iteration 16, loss = 1.15696524
Iteration 17, loss = 1.14849540
Iteration 18, loss = 1.13595711
Iteration 19, loss = 1.12415289
Iteration 20, loss = 1.11558918
Iteration 21, loss = 1.10535424
Iteration 22, loss = 1.09766580
Iteration 23, loss = 1.08931812
Iteration 24, loss = 1.08191449
Iteration 25, loss = 1.07142328
Iteration 26, loss = 1.06699309
Iteration 27, loss = 1.06128824
Iteration 28, loss = 1.05145604
Iteration 29, loss = 1.04566336
Iteration 30, loss = 1.03984590
Iteration 31, loss = 1.03214529
Iteration 32, los

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='adam', tol=0.0001,
              validation_fraction=0.1, verbose=True, warm_start=False)

In [161]:
evaluate_model(X_train, y_train, X_test, y_test, mlp_model)

Training accuracy: 0.70, evaluation accuracy: 0.68


Save models to pkl

In [162]:
pickle.dump(mlp_model, open("ai_model_mlp.pkl","wb"))

In [167]:
!bash evaluate-ai.sh

evaluation of logit
evaluation logit with 10 attempts, resulted with, avg time: 6.71429 and avg score: 8.85714
evaluation of xgb
evaluation xgb with 10 attempts, resulted with, avg time: 5.54286 and avg score: 8.21429
evaluation of mlp
evaluation mlp with 10 attempts, resulted with, avg time: 4.84286 and avg score: 8.17143
evaluation of forest
evaluation forest with 10 attempts, resulted with, avg time: 5.5 and avg score: 8.3


In [ ]:
# model_p = pickle.load(open("ai_model.pkl","rb"))
game_state_4f = (np.array([8,280,630,-1,1,674,-3,7,667,-1,2,649,-3,2,662,0,3,662,-1,4,655,-1,5,608,2,7,1,8,288,630,-1,1,672,-3,7,668,-1,2,650,-3,2,661,0,3,657,-1,4,649,-1,5,602,2,7,1,8,296,629,-1,1,670,-3,7,669,-1,2,651,-3,2,660,0,3,651,-1,4,643,-1,5,596,2,7,1,8,296,628,-1,1,665,-3,7,667,-1,2,650,-3,2,658,0,3,647,-1,4,638,-1,5,589,2,7])
                 .reshape(1, -1))

game_state_1f = (np.array([25, -410, 308, 5, 1, -343, 483, 1, 2, -417, 592, 5, 2, -184, 589, 1, 2, -222, 275, 7, 2, -93, 143, 3, -2, -128, 549, 1, -3, -121, 399, 6, -3]).reshape(1, -1))

xgb_model.predict(game_state_1f)